In [1]:
from lxml import etree
import requests
import pandas as pd

In [2]:
def getLinksAndBarcodes(local_mms_id):
    cont=requests.get('https://open-na.hosted.exlibrisgroup.com/alma/43ACC_ONB/bf/entity/instance/' + local_mms_id).content
    e = etree.XML(cont)
    namespaces = {
        'rdf': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#',
        'bf': 'http://id.loc.gov/ontologies/bibframe/',
        'rdfs': 'http://www.w3.org/2000/01/rdf-schema#',
        'bflc': 'http://id.loc.gov/ontologies/bflc/'
    }
    result = e.xpath('/rdf:RDF/bf:Instance/bf:hasItem/bf:Item/bf:electronicLocator/rdfs:Resource/bflc:locator/@rdf:resource', namespaces=namespaces)
    barcodes = []
    for link in result:
        splits = link.split('%2B')
        if len(splits) >= 2:
            barcodes.append('+' + link.split('%2B')[1])
    print (local_mms_id + ': ' + ", ".join(barcodes))
    linksJoined = ", ".join(result)
    barcodesJoined = ", ".join(barcodes)
    return [linksJoined, barcodesJoined]

In [11]:
df = pd.read_excel('ABOExamplesFromALMA.xlsx')
df_sample = df.sample(3).copy()
df_sample['MMS-ID']

NaN    990032334150603338
NaN    990035648370603338
NaN    990031644540603338
Name: MMS-ID, dtype: int64

In [12]:
df_sample[['Viewerlinks','Barcodes']] = df_sample.apply(lambda row: getLinksAndBarcodes(str(row['MMS-ID'])), axis=1, result_type='expand')

990032334150603338: +Z227525900, +Z172047601


990035648370603338: +Z219890307, +Z255756803


990031644540603338: +Z136879807, +Z172905502


In [15]:
writer = pd.ExcelWriter(r'ABOExamplesFromALMAextended.xlsx', engine='xlsxwriter',options={'strings_to_urls': False})
df_sample.to_excel(writer)
writer.close()